# Strategy Testing

## Strategy Description

### What is Granger?

### Iteration 1
- Using rolling single pair granger causality tests to determine which tokens are causal at any one point in time
- At that point, fit a multivaraite rolling granger causality to predict the next data point
- Trade with size determined by goodness of fit and predicted change 

- Vary across different time frames
- Keep window size fixed (1hr for minute data, 24 hr for hour data, 30 days for daily data)
#
___

In [3]:
# imports
import os
import sys
import logging
import warnings
import logging
from itertools import combinations

# add the parent directory to the path
sys.path.append(os.path.dirname(os.path.abspath('')))
from src.data.data_processor import DataProcessor
from src.visualization.causality_viz import CausalityVisualizer
from src.analysis.causality import CausalityAnalyzer
from src.analysis.granger_causality import AutomatedGrangerAnalyzer
from src.analysis.stationarity import StationarityTester
from src.analysis.outliers import OutlierAnalyzer
from src.analysis.time_varying_granger import run_tvgc_analysis
from src.utils.helpers import calculate_returns
from src.utils.load_data import load_parquet_data

from scipy import stats
import plotly.express as px
import pandas as pd
import matplotlib.pyplot as plt
import statsmodels.api as sm
from statsmodels.tsa.api import VAR


### 1. Load Data

In [151]:
data_dir = "../data/processed"
interval = "1h"

log_returns = {}
prices = {}
# load the data
for time in ['1m', '1h', '1d']:
    returns, prices[time] = load_parquet_data(data_dir=data_dir, interval=time)
    log_returns[time] = pd.DataFrame({key: returns[key].set_index('timestamp')["log_returns"] for key in returns.keys()}).dropna()


2025-01-09 12:38:04 - INFO - Initializing analyzer with data directory: ../data/processed
2025-01-09 12:38:04 - INFO - Starting data loading process...
2025-01-09 12:38:04 - INFO - Looking for parquet files in: c:\Users\owooding\Documents\GraduateScheme\Projects\CryptoCausality\data\processed
2025-01-09 12:38:04 - INFO - Found 24 parquet files
2025-01-09 12:38:04 - INFO - Processing file for ADAUSDT
2025-01-09 12:38:04 - INFO - Processing file for ADAUSDT
2025-01-09 12:38:04 - INFO - Processing file for ADAUSDT
2025-01-09 12:38:04 - INFO - Processing file for ADAUSDT
2025-01-09 12:38:04 - INFO - Loaded 308161 rows for ADAUSDT
2025-01-09 12:38:04 - INFO - Calculating simple returns for ADAUSDT
2025-01-09 12:38:04 - INFO - Calculating price difference for ADAUSDT
2025-01-09 12:38:04 - INFO - Calculating log returns for ADAUSDT
2025-01-09 12:38:04 - INFO - Successfully processed ADAUSDT
2025-01-09 12:38:04 - INFO - Processing file for BNBUSDT
2025-01-09 12:38:04 - INFO - Processing file f

In [152]:
def plot_time_series_data(data, column="close", title=None, symbol=None):
    if symbol != None: 
        fig = px.line(data[f'{symbol}USDT'], x="timestamp", y=column, title=f"{symbol} Close Price", height=500)  
        fig.show()
    else: 
        for symbol in data.keys():
            fig = px.line(data[symbol], x="timestamp", y=column, title=f"{symbol} Close Price", height=300)  
            fig.show()
    

plot_time_series_data(prices['1h'], column="close", title="Close Price")

### 2. Load Causal test data

**How results are used and interpreted**

- Time varying granger causality results for each pair in a single granger rolling model. Each model is run on 10 days of minute data with a rolling window of 300 minutes (5 hours) and a max lag of 100 minutes. 
- Gives the f-stat and p-value for each timestep which indicates the effectiveness of a multivariate OLS vs an autoregressive model over the window specified. 
- At each timestep, we should see which tokens are significant (p-value<0.5) and use them in a new multivariate VAR model to predict the next value of the target variable. 

*(Admittedly, the VAR model seems superior and should be used in isolation on a rolling basis but the impact of only using bivariate granger to determine the VAR variables may also be of interest. Both should be compared)*

**Issues**

- Only 10 days of data for initial test due to large computational requirement of rolling granger


**Assumptions**

To reduce the computational burden, a couple of assumptions are made...
- max lag: window should be restrained to 10: 1. it seems highly unlikely that there would be any value in data more than 10 minutes old. 2. Although in prior experimentation it is seen that upto a lag of 60 may be significant, lags below 10 also show high significance in comparison and so should equally produce good returns if the strategy is profitable. *Further lag analysis in future would be used if a MVP can be produced.*
- rolling window: This window should be balanced to control computational burden and the information included in training each prediction. For minute data, a window of 5 hours (300 min) seems sensible to capture emerging patterns. *A further analysis varying this should be conducted in future.*


In [153]:
# ANALYSIS VARS
TOKEN = "BTCUSDT"
INTERVAL = "1m"
RESULTS_DIR = "../results"

### **Reflection**

- the model seems to work but the VAR disagrees with the granger causality in many places. (1257 values are not significant out of the 2019 predicted as significant by bi-granger)
- going to give up on this and do a rolling VAR with every coin, every time-step. 
- VAR lets you pull out the prediction for all variables at once - a trick to speed up calculations is to fit once, pull out all variable predictions. 
- Do we want any exogenous variables? 

*Next Step*

- We created a faster time-varying multi var predictor with a few key features:
    - multithreading.
    - jump fitting where a model is fit every n timesteps and then used to forecast for the next n timesteps such that there is a forecast for every increment of data but a model fit less frequently.
    - saving result frequently and loading where necessary. 

> Results from the updated model are shown next

**TESTS RUN**

1. 1min data for the period 01-09-2024 : 01-01-2025 (3 months)
    - Max lag = 10
    - Window = 300
    - Fit frequency = 5

2. 1h data for the period 2023-01-01 : 2025-01-01 (2 years)
    - Max lag = 12
    - Window = 120 (5 days)
    - Fit frequency = 1

3. 1d data for the period 2020-01-01 : 2025-01-01 (5 years)
    - Max lag = 10
    - Window = 100
    - Fit frequency = 1



In [154]:
# loading in the results data from database
import sqlite3

def load_from_db(tokens, db_file="../results/results.db"):
    conn = sqlite3.connect(db_file)
    result_dict = {}
    lag_order = pd.read_sql("SELECT * FROM lag_order", conn, index_col='timestamp')
    result_dict['lag_order'] = lag_order
    for token in tokens:
        stats = pd.read_sql(f"SELECT * FROM {token}_stats", conn, index_col='timestamp')
        preds = pd.read_sql(f"SELECT * FROM {token}_preds", conn, index_col='timestamp')

        # save data a corect types
        stats['p_value'] = stats['p_value'].astype(float)
        stats['f_stat'] = stats['f_stat'].astype(float)
        preds['pred'] = preds['pred'].astype(float)
        preds['significant_tokens'] = preds['significant_tokens'].astype(str)

        result_dict[token] = {'stats': stats, 'preds': preds}
    conn.close()
    return result_dict


In [182]:
# load results
results_file_1m = "../results/1m/1m_results.db"
results_file_1h = "../results/1h/1h_results.db"
results_file_1d = "../results/1d/1d_results.db"
tokens = log_returns['1m'].columns

results_1m = load_from_db(tokens, db_file=results_file_1m)
results_1h = load_from_db(tokens, db_file=results_file_1h)
results_1d = load_from_db(tokens, db_file=results_file_1d)

# separate and prepare results data
def prepare_db_results(results_dict: dict, returns: pd.DataFrame): 
    lag_order = results_dict['lag_order'].dropna()
    lag_order = lag_order[lag_order['lag_order']!=0]

    results = {}
    for token in results_dict.keys():
        if token != 'lag_order':
            # remove na and duplicates
            stats = results_dict[token]['stats'].dropna()
            stats = stats.reset_index().drop_duplicates(subset='timestamp', keep='last').set_index('timestamp')
            
            preds = results_dict[token]['preds'].dropna()
            preds = preds.reset_index().drop_duplicates(subset='timestamp', keep='last').set_index('timestamp')
            preds['act'] = returns.shift(-1).reset_index().drop_duplicates(subset='timestamp', keep='last').set_index('timestamp')[token]
            lag_order = lag_order[lag_order.index.isin(stats.index)]
            results[token] = pd.concat([stats, preds], axis=1)
            results[token].index = pd.to_datetime(results[token].index)
    return results

results_1m = prepare_db_results(results_1m, log_returns['1m'])
results_1h = prepare_db_results(results_1h, log_returns['1h'])
results_1d = prepare_db_results(results_1d, log_returns['1d'])


In [183]:
# plot the results and predictions for each token
TOKEN = "BTCUSDT"

fig = px.line()

# Add log returns to the plot
fig.add_scatter(x=results_1m[TOKEN].index, y=results_1m[TOKEN]['act'], mode='lines', name='Log Returns')

# Ensure y values are numeric
y_values = pd.to_numeric(results_1m[TOKEN]['pred'], errors='coerce')

# Add predictions to the plot
fig.add_scatter(x=results_1m[TOKEN].index, y=y_values, mode='lines', name='Predictions')

# Update layout
fig.update_layout(title=f'Log Returns vs Predictions for {TOKEN}', xaxis_title='Time', yaxis_title='Value')

fig.show()

In [184]:
def mean_absolute_error(actual, predicted):
    return sum(abs(a - p) for a, p in zip(actual, predicted)) / len(actual)

def mean_squared_error(actual, predicted):
    return sum((a - p) ** 2 for a, p in zip(actual, predicted)) / len(actual)

def r2_score(actual, predicted):
    mean_actual = sum(actual) / len(actual)
    ss_total = sum((a - mean_actual) ** 2 for a in actual)
    ss_residual = sum((a - p) ** 2 for a, p in zip(actual, predicted))
    return 1 - (ss_residual / ss_total)

def analyze_prediction_accuracy(results, token):
    actual = results[token]['act'][:-1]
    predicted = results[token]['pred'][:-1]

    mae = mean_absolute_error(actual, predicted)
    mse = mean_squared_error(actual, predicted)
    r2 = r2_score(actual, predicted)

    print(f"Accuracy Analysis for {token}:")
    print(f"Mean Absolute Error (MAE): {mae}")
    print(f"Mean Squared Error (MSE): {mse}")
    print(f"R-squared (R²): {r2}")

# Perform the analysis for the specified token
analyze_prediction_accuracy(results_1m, TOKEN)

Accuracy Analysis for BTCUSDT:
Mean Absolute Error (MAE): 0.0004689123907219803
Mean Squared Error (MSE): 5.386282327479143e-07
R-squared (R²): -0.12336096707402566


In [185]:
# Example easy strategy
import numpy as np

def test_signal(results, token, threshold=0.5):
    preds = results[token]['pred']
    actual = results[token]['act']
    signal = np.where(preds > threshold, 1, np.where(preds < -threshold, -1, 0))
    return signal

# calculate reutrns
def calculate_returns(data, signal, token):
    returns = data[token]
    returns = pd.DataFrame(returns)
    returns['signal'] = signal
    returns['returns'] = returns[token].pct_change()
    returns['strategy'] = returns['signal'] * returns['returns']
    return returns